In [1]:
import sys
sys.path.insert(0, '../')
sys.path.insert(0, '../datasets')

In [2]:
import csv
import os

import numpy as np
import torch
import torch.utils.data as data
import torchvision
from numpy.random import randint

import transforms as t

from video_dataset import VideoRecord


class Charades(data.Dataset):
    """ Charades Dataset.
    Args:
        root_path: Full path to the dataset videos directory.
        list_file: Full path to the file that lists the videos to be considered (train, val, test)
            with its annotations.
        sample_frames: Number of frames used in the input (temporal dimension).
        transform: A function that takes in an PIL image and returns a transformed numpy version.
        mode: Set the dataset mode as 'train', 'val' or 'test'.
        test_clips: Number of clips to be evenly sample from each full-length video for evaluation.
        causal: If True, sets the evaluation to causal mode. (NotImplemented)
    """
    input_mean = [0.485, 0.456, 0.406]
    input_std = [0.229, 0.224, 0.225]
    FPS, GAP = 24, 4
    num_classes = 157
    multi_label = True

    def __init__(self, root_path, list_file, sample_frames=8, transform=None,
                 mode='train', test_clips=10, causal=False):
        self.root_path = root_path
        self.list_file = list_file
        self.sample_frames = sample_frames
        self.stride = 2 if sample_frames == 32 else 8
        self.mode = mode
        self.test_clips = test_clips
        self.causal = causal

        if transform is not None:
            self.transform = transform
        else:
            self.transform = self.default_transforms()

        self._parse_list()

    def _parse_list(self):
        """
        Parses the annotation file to create a list of the videos relative path and their labels
        in the format: [label, video_path].
        """
        video_list = []
        self.total_frames = 0
        with open(self.list_file) as f:
            reader = csv.DictReader(f)
            for row in reader:
                vid = row['id']
                actions = row['actions']
                self.total_frames += int(float(row['length']) * self.FPS)
                if actions == '':
                    actions = []
                else:
                    actions = [a.split(' ') for a in actions.split(';')]
                    actions = [{'class': x, 'start': float(
                        y), 'end': float(z)} for x, y, z in actions]
                video_list.append([actions, vid])

        # Subset for tests!!!
        subset_list = [v for i, v in enumerate(video_list) if i % 10 == 0]

        self.video_list = subset_list

    def get_weights(self):
        pos_frames_per_class = torch.FloatTensor(self.num_classes).zero_()
        for i, (label, _) in enumerate(self.video_list):
            for l in label:
                frame_start = int(l['start'] * self.FPS)
                frame_end = int(l['end'] * self.FPS)
                pos_frames_per_class[int(l['class'][1:])] += frame_end - frame_start
        pos_weigth = torch.FloatTensor([(self.total_frames-p)/p for p in pos_frames_per_class])

        return pos_weigth.cuda() if torch.cuda.is_available() else pos_weigth

    def _get_train_indices(self, record):
        """
        Args:
            record : VideoRecord object
        Returns:
            offsets : List of image indices to be loaded from a video.
            target: Binary list of labels from a video.
        """
        expanded_sample_length = self.sample_frames * self.stride
        if record.num_frames >= expanded_sample_length:
            start_pos = randint(record.num_frames - expanded_sample_length + 1)
            offsets = range(start_pos, start_pos + expanded_sample_length, self.stride)
        elif record.num_frames > self.sample_frames:
            start_pos = randint(record.num_frames - self.sample_frames + 1)
            offsets = range(start_pos, start_pos + self.sample_frames, 1)
        else:
            offsets = np.sort(randint(record.num_frames, size=self.sample_frames))
        print(record.label)
        print(min(offsets)/float(self.FPS), max(offsets)/float(self.FPS))
        target = torch.IntTensor(self.num_classes).zero_()
        for frame in offsets:
            for l in record.label:
                if l['start'] < frame/float(self.FPS) < l['end']:
                    print(l, int(l['class'][1:]))
                    target[int(l['class'][1:])] = 1

        return offsets, target

    def _get_test_indices(self, record):
        """
        Args:
            record : VideoRecord object
        Returns:
            offsets : List of image indices to be loaded from a video.
            target: Binary list of labels from a video.
        """
        sample_start_pos = np.linspace(
            self.sample_frames*self.stride, record.num_frames-1, self.test_clips, dtype=int)
        offsets = []
        for p in sample_start_pos:
            offsets.extend(np.linspace(
                max(p-self.sample_frames*self.stride + self.stride, 0),
                min(p, record.num_frames-1),
                self.sample_frames, dtype=int))

        target = torch.IntTensor(self.num_classes).zero_()
        for l in record.label:
            target[int(l['class'][1:])] = 1

        return offsets, target

    def __getitem__(self, index):
        label, video_path = self.video_list[index]
        record = VideoRecord(os.path.join(self.root_path, video_path+'.mp4'), label)

        if self.mode == 'train':
            segment_indices, target = self._get_train_indices(record)
            process_data = self.get(record, segment_indices)
            while process_data is None:
                index = randint(0, len(self.video_list) - 1)
                process_data, target = self.__getitem__(index)
        else:
            segment_indices, target = self._get_test_indices(record)
            process_data = self.get(record, segment_indices)
            if process_data is None:
                raise ValueError('sample indices:', record.path, segment_indices)

        data = process_data.squeeze(0)
        data = data.view(3, -1, self.sample_frames, data.size(2), data.size(3)).contiguous()
        data = data.permute(1, 0, 2, 3, 4).contiguous()

        return data, {'target': target, 'video_path': video_path}

    def get(self, record, indices):
        uniq_id = np.unique(indices)
        uniq_imgs = record.get_frames(uniq_id)

        if None in uniq_imgs:
            return None

        images = [uniq_imgs[i] for i in indices]
        images = self.transform(images)
        return images

    def __len__(self):
        return len(self.video_list)

    def default_transforms(self):
        """
        Returns:
            A transform function to be applied in the PIL images.
        """
        if self.mode == 'val':
            cropping = torchvision.transforms.Compose([
                t.GroupResize(256),
                t.GroupCenterCrop(224)
            ])
        elif self.mode == 'test':
            cropping = torchvision.transforms.Compose([
                t.GroupResize(256),
                t.GroupFullyConv(320)
            ])
        elif self.mode == 'train':
            cropping = torchvision.transforms.Compose([
                t.GroupRandomResize(256, 320),
                t.GroupRandomCrop(224),
                t.GroupResize(288),
                t.GroupRandomHorizontalFlip()
            ])
        else:
            raise ValueError('Mode {} does not exist. Choose between: val, test or train.'.format(
                self.mode))

        transforms = torchvision.transforms.Compose([
                cropping,
                t.GroupToTensorStack(),
                t.GroupNormalize(mean=self.input_mean, std=self.input_std)
            ])

        return transforms

    def __repr__(self):
        fmt_str = 'Dataset ' + self.__class__.__name__ + '\n'
        fmt_str += '    Number of samples: {}\n'.format(self.__len__())
        fmt_str += '    Videos Location: {}\n'.format(self.root_path)
        fmt_str += '    Annotations file: {}\n'.format(self.list_file)
        fmt_str += '    Test clips: {}\n'.format(self.test_clips) if self.mode != 'train' else ''
        tmp = ' (multi-label)' if self.multi_label else ''
        fmt_str += '    Number of classes: {}{}\n'.format(self.num_classes, tmp)
        tmp = '    Transforms (if any): '
        fmt_str += '{0}{1}\n'.format(tmp,
                                     self.transform.__repr__().replace('\n', '\n' + ' ' * len(tmp)))

        return fmt_str


In [3]:
root_data_path = '../../../../Datasets/Charades/Charades_v1_480'
map_file = '../../../../Datasets/Charades/Annotations/Charades_v1_train.csv'

dataset = Charades(root_data_path, map_file, sample_frames=32, mode='train')
data_loader = torch.utils.data.DataLoader(
    dataset, batch_size=1, shuffle=False, num_workers=1)

In [4]:
total_num = len(data_loader.dataset)
data_gen = enumerate(data_loader, start=1)

for i, (data, label) in data_gen:
    print(label)
    if 1 >2:
        raise Exception

[{'class': 'c092', 'start': 11.9, 'end': 21.2}, {'class': 'c147', 'start': 0.0, 'end': 12.6}]
3.1666666666666665 5.75
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147
{'class': 'c147', 'start': 0.0, 'end': 12.6} 147


{'class': 'c009', 'start': 4.1, 'end': 12.9} 9
{'class': 'c107', 'start': 0.0, 'end': 10.3} 107
{'class': 'c131', 'start': 5.1, 'end': 14.5} 131
{'class': 'c152', 'start': 5.1, 'end': 14.5} 152
{'class': 'c132', 'start': 0.6, 'end': 11.2} 132
{'class': 'c109', 'start': 5.5, 'end': 13.6} 109
{'class': 'c009', 'start': 4.1, 'end': 12.9} 9
{'class': 'c107', 'start': 0.0, 'end': 10.3} 107
{'class': 'c131', 'start': 5.1, 'end': 14.5} 131
{'class': 'c152', 'start': 5.1, 'end': 14.5} 152
{'class': 'c132', 'start': 0.6, 'end': 11.2} 132
{'class': 'c109', 'start': 5.5, 'end': 13.6} 109
{'class': 'c009', 'start': 4.1, 'end': 12.9} 9
{'class': 'c107', 'start': 0.0, 'end': 10.3} 107
{'class': 'c131', 'start': 5.1, 'end': 14.5} 131
{'class': 'c152', 'start': 5.1, 'end': 14.5} 152
{'class': 'c132', 'start': 0.6, 'end': 11.2} 132
{'class': 'c109', 'start': 5.5, 'end': 13.6} 109
{'class': 'c009', 'start': 4.1, 'end': 12.9} 9
{'class': 'c107', 'start': 0.0, 'end': 10.3} 107
{'class': 'c131', 'start': 5

[{'class': 'c020', 'start': 23.6, 'end': 29.8}, {'class': 'c152', 'start': 0.0, 'end': 3.5}, {'class': 'c016', 'start': 0.0, 'end': 15.8}, {'class': 'c015', 'start': 0.0, 'end': 28.0}, {'class': 'c023', 'start': 23.1, 'end': 32.0}, {'class': 'c156', 'start': 14.4, 'end': 32.0}, {'class': 'c062', 'start': 12.7, 'end': 32.0}, {'class': 'c061', 'start': 13.5, 'end': 20.2}, {'class': 'c097', 'start': 26.5, 'end': 32.0}]
17.291666666666668 19.875
{'class': 'c015', 'start': 0.0, 'end': 28.0} 15
{'class': 'c156', 'start': 14.4, 'end': 32.0} 156
{'class': 'c062', 'start': 12.7, 'end': 32.0} 62
{'class': 'c061', 'start': 13.5, 'end': 20.2} 61
{'class': 'c015', 'start': 0.0, 'end': 28.0} 15
{'class': 'c156', 'start': 14.4, 'end': 32.0} 156
{'class': 'c062', 'start': 12.7, 'end': 32.0} 62
{'class': 'c061', 'start': 13.5, 'end': 20.2} 61
{'class': 'c015', 'start': 0.0, 'end': 28.0} 15
{'class': 'c156', 'start': 14.4, 'end': 32.0} 156
{'class': 'c062', 'start': 12.7, 'end': 32.0} 62
{'class': 'c061

{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4, 'end': 31.7} 130
{'class': 'c062', 'start': 0.4, 'end': 31.4} 62
{'class': 'c130', 'start': 4.4

{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 17.7} 52
{'class': 'c059', 'start': 0.0, 'end': 20.0} 59
{'class': 'c011', 'start': 0.0, 'end': 19.6} 11
{'class': 'c052', 'start': 0.0, 'end': 1

...

{'class': 'c144', 'start': 0.0, 'end': 24.0} 144
{'class': 'c020', 'start': 0.0, 'end': 32.0} 20
{'class': 'c106', 'start': 5.9, 'end': 32.0} 106
{'class': 'c033', 'start': 0.0, 'end': 23.3} 33
{'class': 'c144', 'start': 0.0, 'end': 24.0} 144
{'class': 'c020', 'start': 0.0, 'end': 32.0} 20
{'class': 'c106', 'start': 5.9, 'end': 32.0} 106
{'class': 'c033', 'start': 0.0, 'end': 23.3} 33
{'class': 'c144', 'start': 0.0, 'end': 24.0} 144
{'class': 'c020', 'start': 0.0, 'end': 32.0} 20
{'class': 'c106', 'start': 5.9, 'end': 32.0} 106
{'class': 'c033', 'start': 0.0, 'end': 23.3} 33
{'class': 'c144', 'start': 0.0, 'end': 24.0} 144
{'class': 'c020', 'start': 0.0, 'end': 32.0} 20
{'class': 'c106', 'start': 5.9, 'end': 32.0} 106
{'class': 'c033', 'start': 0.0, 'end': 23.3} 33
{'class': 'c144', 'start': 0.0, 'end': 24.0} 144
{'class': 'c020', 'start': 0.0, 'end': 32.0} 20
{'class': 'c106', 'start': 5.9, 'end': 32.0} 106
{'class': 'c033', 'start': 0.0, 'end': 23.3} 33
{'class': 'c144', 'start': 0.0

{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c118', 'start': 2.3, 'end': 32.0} 118
{'class': 'c106', 'start': 11.1, 'end': 29.9} 106
{'class': 'c110', 'start': 2.3, 'end': 32.0} 110
{'class': 'c1

{'target': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]], dtype=torch.int32), 'video_path': ['5657O']}
[{'class': 'c137', 'start': 0.0, 'end': 32.0}, {'class': 'c033', 'start': 0.0, 'end': 32.0}, {'class': 'c149', 'start': 0.0, 'end': 32.0}, {'class': 'c152', 'start': 0.0, 'end': 32.0}]
30.291666666666668 32.875
{'class': 'c137', 'start': 0.0, 'end': 32.0} 137
{'class': 'c033', 'start': 0.0, 'end': 32.0} 33
{'class': 'c149', 'start': 0.0, 'end': 32.0} 149
{'class': 'c152', 'start': 0.0, 'end': 32.0} 152
{'

{'class': 'c056', 'start': 0.0, 'end': 32.0} 56
{'class': 'c107', 'start': 1.7, 'end': 26.6} 107
{'class': 'c118', 'start': 1.7, 'end': 26.6} 118
{'class': 'c123', 'start': 13.3, 'end': 32.0} 123
{'class': 'c063', 'start': 1.7, 'end': 26.6} 63
{'class': 'c056', 'start': 0.0, 'end': 32.0} 56
{'class': 'c107', 'start': 1.7, 'end': 26.6} 107
{'class': 'c118', 'start': 1.7, 'end': 26.6} 118
{'class': 'c123', 'start': 13.3, 'end': 32.0} 123
{'class': 'c063', 'start': 1.7, 'end': 26.6} 63
{'class': 'c056', 'start': 0.0, 'end': 32.0} 56
{'class': 'c107', 'start': 1.7, 'end': 26.6} 107
{'class': 'c118', 'start': 1.7, 'end': 26.6} 118
{'class': 'c123', 'start': 13.3, 'end': 32.0} 123
{'class': 'c063', 'start': 1.7, 'end': 26.6} 63
{'class': 'c056', 'start': 0.0, 'end': 32.0} 56
{'class': 'c107', 'start': 1.7, 'end': 26.6} 107
{'class': 'c118', 'start': 1.7, 'end': 26.6} 118
{'class': 'c123', 'start': 13.3, 'end': 32.0} 123
{'class': 'c063', 'start': 1.7, 'end': 26.6} 63
{'class': 'c056', 'start

{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'class': 'c059', 'start': 0.0, 'end': 16.1} 59
{'target': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]], dtype=torch.int32), 'video_path': ['0L0KS']}
[{'class': 'c065', 'start': 17.6, 'end': 31.0}, {'class': 'c067', 'start